In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/garbage-data/paper_data.yaml
/kaggle/input/garbage-data/data.yaml
/kaggle/input/garbage-data/paper/paper-1/README.dataset.txt
/kaggle/input/garbage-data/paper/paper-1/README.roboflow.txt
/kaggle/input/garbage-data/paper/paper-1/data.yaml
/kaggle/input/garbage-data/paper/paper-1/valid/labels/paper402_jpeg_jpg.rf.b408c6a16a85d36321cd1058222538c2.txt
/kaggle/input/garbage-data/paper/paper-1/valid/labels/20220216_190558_jpg.rf.a855af050035923f581cb656f8da6c97.txt
/kaggle/input/garbage-data/paper/paper-1/valid/labels/paper1959_jpg.rf.73b570e517b767c83e9bd60c53a1cbaf.txt
/kaggle/input/garbage-data/paper/paper-1/valid/labels/paper760_jpg.rf.2ef3f234974b8e9f2ff9d9dcedf12c3c.txt
/kaggle/input/garbage-data/paper/paper-1/valid/labels/paper1491_jpeg_jpg.rf.c37daf70137b6a98286909a298d061b1.txt
/kaggle/input/garbage-data/paper/paper-1/valid/labels/20220216_203938_jpg.rf.6e9764f199a939e03800383cf85365e4.txt
/kaggle/input/garbage-data/paper/paper-1/valid/labels/paper1889_jpg.rf.0d8e817c3

In [2]:
# ===============================
# STEP 1: Install EfficientNet
# ===============================
!pip install -q efficientnet_pytorch

# ===============================
# STEP 2: Import Libraries
# ===============================
import os
import torch
import torchvision.transforms as transforms
from torch.utils.data import Dataset, DataLoader
from efficientnet_pytorch import EfficientNet
import torch.nn as nn
import torch.optim as optim
from torch.optim.lr_scheduler import ReduceLROnPlateau
from tqdm import tqdm
from PIL import Image
from collections import Counter

# ===============================
# STEP 3: Setup Device and Dataset Path
# ===============================
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print("Using device:", device)

# Define the dataset path
data_dir = '/kaggle/input/garbage-data/YOLO-Waste-Detection-1/YOLO-Waste-Detection-1'

# Class names (44 classes)
class_names = [
    "Aerosols", "Aluminum can", "Aluminum caps", "Cardboard", "Cellulose", "Ceramic", 
    "Combined plastic", "Container for household chemicals", "Disposable tableware", 
    "Electronics", "Foil", "Furniture", "Glass bottle", "Iron utensils", "Liquid", 
    "Metal shavings", "Milk bottle", "Organic", "Paper bag", "Paper cups", "Paper shavings", 
    "Paper", "Papier mache", "Plastic bag", "Plastic bottle", "Plastic can", "Plastic canister", 
    "Plastic caps", "Plastic cup", "Plastic shaker", "Plastic shavings", "Plastic toys", 
    "Postal packaging", "Printing industry", "Scrap metal", "Stretch film", "Tetra pack", 
    "Textile", "Tin", "Unknown plastic", "Wood", "Zip plastic bag", "Ramen Cup", "Food Packet"
]

nc = 44  # Number of classes

# ===============================
# STEP 4: Define Custom Dataset for YOLO Format (Classifying images)
# ===============================
class YOLODataset(Dataset):
    def __init__(self, data_dir, transform=None, mode='train'):
        self.data_dir = data_dir
        self.transform = transform
        self.image_dir = os.path.join(data_dir, mode, 'images')
        self.label_dir = os.path.join(data_dir, mode, 'labels')
        self.image_paths = [os.path.join(self.image_dir, f) for f in os.listdir(self.image_dir) if f.endswith('.jpg')]
        
    def __len__(self):
        return len(self.image_paths)
    
    def __getitem__(self, idx):
        image_path = self.image_paths[idx]
        label_path = os.path.join(self.label_dir, os.path.basename(image_path).replace('.jpg', '.txt'))
        
        # Load image
        image = Image.open(image_path).convert("RGB")
        
        # Load labels (class IDs)
        class_ids = []
        with open(label_path, 'r') as file:
            for line in file:
                parts = line.strip().split()
                class_id = int(parts[0])  # Class ID
                class_ids.append(class_id)  # Only keep class ID, not bounding boxes
        
        # For classification, choose the most frequent class in the image
        if len(class_ids) > 0:
            label = Counter(class_ids).most_common(1)[0][0]  # Most frequent class ID
        else:
            label = 0  # Default to a class (if there are no objects, for example)
        
        # Apply transforms
        if self.transform:
            image = self.transform(image)
        
        return image, label

# ===============================
# Custom Collate Function to Handle Different Sizes (only class IDs for classification)
# ===============================
def collate_fn(batch):
    images = []
    labels = []
    
    for image, label in batch:
        images.append(image)
        labels.append(label)
    
    # Stack images and labels
    images = torch.stack(images)
    labels = torch.tensor(labels)
    
    return images, labels

# ===============================
# STEP 5: Define Transforms & Data Loaders with Custom Collate Function
# ===============================
train_transform = transforms.Compose([
    transforms.Resize((300, 300)),
    transforms.RandomHorizontalFlip(),
    transforms.RandomRotation(15),
    transforms.ColorJitter(brightness=0.2, contrast=0.2),
    transforms.RandomResizedCrop(300, scale=(0.8, 1.0)),
    transforms.ToTensor(),
])

val_transform = transforms.Compose([
    transforms.Resize((300, 300)),
    transforms.ToTensor(),
])

# Load dataset and split into train, validation
train_dataset = YOLODataset(data_dir, transform=train_transform, mode='train')
val_dataset = YOLODataset(data_dir, transform=val_transform, mode='valid')

train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True, collate_fn=collate_fn)
val_loader = DataLoader(val_dataset, batch_size=32, collate_fn=collate_fn)

print("Dataset loaded with", len(train_dataset), "training images and", len(val_dataset), "validation images")

# ===============================
# STEP 6: Load Model and Prepare for Training
# ===============================
model = EfficientNet.from_pretrained('efficientnet-b0')
model._fc = nn.Linear(model._fc.in_features, nc)  # Adjust for 44 classes
model.to(device)

criterion = nn.CrossEntropyLoss()  # For classification task
optimizer = optim.Adam(model.parameters(), lr=1e-4)
scheduler = ReduceLROnPlateau(optimizer, mode='min', factor=0.5, patience=2, verbose=True)

# ===============================
# STEP 7: Training Loop with Early Stopping
# ===============================
best_val_loss = float('inf')
patience = 5
epochs_no_improve = 0
num_epochs = 1000  # Change this to the desired number of epochs
checkpoint_path = 'best_model.pth'

for epoch in range(num_epochs):
    print(f"\nEpoch {epoch+1}/{num_epochs}")
    
    # --- Training ---
    model.train()
    train_loss = 0.0
    for images, labels in tqdm(train_loader):
        images, labels = images.to(device), labels.to(device)
        optimizer.zero_grad()
        outputs = model(images)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        train_loss += loss.item()
    avg_train_loss = train_loss / len(train_loader)

    # --- Validation ---
    model.eval()
    val_loss = 0.0
    correct = 0
    total = 0
    with torch.no_grad():
        for images, labels in val_loader:
            images, labels = images.to(device), labels.to(device)
            outputs = model(images)
            loss = criterion(outputs, labels)
            val_loss += loss.item()
            _, preds = torch.max(outputs, 1)
            correct += (preds == labels).sum().item()
            total += labels.size(0)
    avg_val_loss = val_loss / len(val_loader)
    val_acc = 100 * correct / total

    print(f"Train Loss: {avg_train_loss:.4f} | Val Loss: {avg_val_loss:.4f} | Val Acc: {val_acc:.2f}%")
    scheduler.step(avg_val_loss)

    # --- Save Best Model ---
    if avg_val_loss < best_val_loss:
        best_val_loss = avg_val_loss
        epochs_no_improve = 0
        torch.save(model.state_dict(), checkpoint_path)
        print(">> Model saved as best checkpoint")
    else:
        epochs_no_improve += 1
        if epochs_no_improve >= patience:
            print(">> Early stopping!")
            break

# ===============================
# STEP 8: Save Final Model
# ===============================
final_model_path = '/kaggle/working/efficientnet_garbage_classifier.pth'
torch.save(model.state_dict(), final_model_path)
print(f"\n>> Final model saved to: {final_model_path}")


  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 8.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 29.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 13.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 76.3 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
pylibcugraph-cu12 24.12.0 requires pylibraft-cu12==24.12.*, but you have pylibraft-cu12 25.2.0 which is incompatible.
pylibcugraph-cu12 24.12.0 requires rmm-cu12==24.12.*, but you have rmm-cu12 25.2.0 which is incompatible.
U

Downloading: "https://github.com/lukemelas/EfficientNet-PyTorch/releases/download/1.0/efficientnet-b0-355c32eb.pth" to /root/.cache/torch/hub/checkpoints/efficientnet-b0-355c32eb.pth
100%|██████████| 20.4M/20.4M [00:00<00:00, 163MB/s]


Loaded pretrained weights for efficientnet-b0


/usr/local/lib/python3.11/dist-packages/torch/optim/lr_scheduler.py:62: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn(



Epoch 1/1000


...

Train Loss: 0.0185 | Val Loss: 0.4125 | Val Acc: 92.35%

Epoch 11/1000


100%|██████████| 595/595 [07:31<00:00,  1.32it/s]


Train Loss: 0.0159 | Val Loss: 0.4093 | Val Acc: 92.75%

Epoch 12/1000


100%|██████████| 595/595 [07:40<00:00,  1.29it/s]


Train Loss: 0.0126 | Val Loss: 0.4027 | Val Acc: 92.65%
>> Early stopping!

>> Final model saved to: /kaggle/working/efficientnet_garbage_classifier.pth
